In [1]:
# %pip install --upgrade pip
# %pip install pandas
# %pip install numpy
# %pip install datetime
# %pip install collections
# %pip install matplotlib.pyplot
# %pip install seaborn
# %pip install pyyaml
# %pip install jsonlines
# %pip install requests
# %pip install datasets
# %pip install torch
# %pip install scikit-learn
# %pip install tabulate

# %pip install statsmodels

In [2]:
import sys
import os
import re
import json
import pandas as pd
import numpy as np
import random
import copy
from datetime import datetime
from collections import Counter, defaultdict

import matplotlib.pyplot as plt
import seaborn as sns

sys.path.append("../")

from src.helpers import io
from src.classes.dataset import Dataset
from src.classes.annotation_set import AnnotationSet
from src.helpers.visualisation import barplot_distribution, plot_confusion_matrix, tabulate_annotation_pair_summary, analyze_pair_annotations

%load_ext autoreload
%autoreload 2

## Load Dataset + Annotations

In [3]:
# FILL IN:
PATH_TO_DATASET = "../data/automatic_annotations_v0/wildchat4k-raw.json"
DATASET_ID = "wildchat_1m"
PATH_TO_ANNOTATIONS_DIR = "../data/automatic_annotations_v0/gpto3mini-json-wildchat"
PATH_TO_LANGUAGE_ANNOTATIONS = "../data/automatic_annotations_v0/annotations_languages.jsonl"

In [4]:
# Load dataset (w/o annotations)
dataset = Dataset.load(PATH_TO_DATASET)

# Load annotations into dataset
for fpath in io.listdir_nohidden(PATH_TO_ANNOTATIONS_DIR):
    annotation_set = AnnotationSet.load_automatic(path=fpath, source="automatic_v0")
    dataset.add_annotations(annotation_set)

prompt-multi_turn_relationship: 0 / 10127 failed due to invalid annotations.
prompt-interaction_features: 0 / 10127 failed due to invalid annotations.
turn-sensitive_use_flags: 20 / 10127 failed due to invalid annotations.
turn-topic: 55 / 10127 failed due to invalid annotations.
response-interaction_features: 0 / 10127 failed due to invalid annotations.
prompt-function_purpose: 103 / 10127 failed due to invalid annotations.
prompt-media_format: 9 / 10127 failed due to invalid annotations.
response-media_format: 0 / 10127 failed due to invalid annotations.
response-answer_form: 0 / 10127 failed due to invalid annotations.


In [5]:
annotation_pairs1 = dataset.get_annotation_distribution(
    "turn_topic",
    level="message",
    annotation_source="automatic_v0",
    annotation_as_list_type=True,
)
annotation_pairs2 = dataset.get_annotation_distribution(
    "turn_topic",
    level="message",
    annotation_source="automatic_v0",
    annotation_as_list_type=False,
)

outdir = f"../data/annotation_analysis_v0/topic"
os.makedirs(outdir, exist_ok=True)
fig = barplot_distribution(
    {"Topics": annotation_pairs1}, normalize=True, 
    xlabel="Topics", ylabel="Proportion", title="",
    output_path=f"{outdir}/barchart.png", order="descending")

multibar_fig = barplot_distribution(
    {"Topics": annotation_pairs2}, normalize=True, 
    xlabel="Topics", ylabel="Proportion", title="",
    output_path=f"{outdir}/multilabel_barchart.png", order="descending")

/Users/chuanyang/Desktop/naturalistic-ai-chuanyang/notebooks/../src/helpers/visualisation.py:125: UserWarning: constrained_layout not applied because axes sizes collapsed to zero.  Try making figure larger or axes decorations smaller.
  fig.savefig(output_path, bbox_inches='tight')


In [8]:
print(dataset.data[0])
print(vars(dataset.data[0]))

{'conversation_id': 'wildchat_553847317a397b5def89dae32fe9defd', 'dataset_id': 'wildchat_1m', 'user_id': '8fe04885ac7d4510a0f7695261f3285dff4529ce91d15f84dc6c5880977a556a', 'time': '2023-04-25T02:20:46+00:00', 'model': 'gpt-3.5-turbo-0301', 'conversation': [<src.classes.message.Message object at 0x111f79e40>, <src.classes.message.Message object at 0x11251a710>, <src.classes.message.Message object at 0x112518d30>, <src.classes.message.Message object at 0x112519c90>, <src.classes.message.Message object at 0x112518850>, <src.classes.message.Message object at 0x11251a020>, <src.classes.message.Message object at 0x11251a170>, <src.classes.message.Message object at 0x11251ad70>, <src.classes.message.Message object at 0x11251bdf0>, <src.classes.message.Message object at 0x112518f10>, <src.classes.message.Message object at 0x112518b80>, <src.classes.message.Message object at 0x112518eb0>, <src.classes.message.Message object at 0x11251a3e0>, <src.classes.message.Message object at 0x11251bd30>, 

In [9]:
annotation_pairs1 = dataset.get_annotation_distribution(
    "turn_topic",
    level="message",
    annotation_source="automatic_v0",
    annotation_as_list_type=True,
)
print(annotation_pairs1)

{"['entertainment hobbies leisure']": 338, "['employment hiring']": 89, "['news current affairs']": 26, "['employment hiring', 'technology software computing']": 4, "['technology software computing']": 1956, "['food dining']": 66, "['culture', 'entertainment hobbies leisure', 'history']": 1, "['art design']": 407, "['fantasy fiction fanfiction']": 610, "['adult illicit content']": 516, "['adult illicit content', 'fantasy fiction fanfiction']": 118, "['adult illicit content', 'art design', 'fantasy fiction fanfiction']": 2, "['fantasy fiction fanfiction', 'news current affairs', 'politics elections', 'social issues movements']": 1, "['none']": 555, "['literature writing']": 214, "['education', 'interpersonal relationships communication', 'lifestyle', 'nature environment', 'technology software computing', 'travel tourism']": 1, "['education', 'linguistics languages']": 27, "['social issues movements']": 30, "['history', 'psychology philosophy human behavior', 'social issues movements']":

In [10]:
[name for name in dir(dataset) if not name.startswith('_')]

['add_annotations',
 'data',
 'dataset_id',
 'extract_all_metadata_values_for_annotation_source_name',
 'extract_conversation_metadata_by_ids',
 'find_conflicting_annotations',
 'find_conversations_by_metadata',
 'get_annotation_distribution',
 'get_confidence_distribution',
 'get_joint_distribution',
 'id_lookup',
 'load',
 'random_sample',
 'save_to_json',
 'slice',
 'to_dict']

In [11]:
from collections import Counter

# Count how many conversations each user_id has
user_counter = Counter()
for conv in dataset.data:
    user_counter[conv.user_id] += 1

# Find the first user_id with more than 100 conversations
for user_id, count in user_counter.items():
    # print(f"User ID: {user_id}, Conversations: {count}")
    if count > 10:
        print(f"First user_id with more than 10 conversations: {user_id} ({count} conversations)")
        # break

First user_id with more than 10 conversations: 2a28eab6a25a22abbe8a2de22f61e06101936bad97e1b8263c5061ade8f872b8 (29 conversations)
First user_id with more than 10 conversations: a89177c80571053584234edca85f348690bf0ab5873876a9486694cd7c15a1fb (22 conversations)
First user_id with more than 10 conversations: 3e7ae36b9ca739b0e16876727814a0e8470c8496aab833c49a5bcc7e77bb7f01 (43 conversations)
First user_id with more than 10 conversations: a5146fac10d0a974d79af83042eed65659396495d293967ddc1b69779ed35179 (21 conversations)
First user_id with more than 10 conversations: dec1f72ae4d94e369602348fc957b0d6781051aa664f2458ee53c19be1740dd7 (21 conversations)
First user_id with more than 10 conversations: a0e542c18e25a29832c7c59ca23d4c90e717b250624cd0ca578bd59670ec05c0 (11 conversations)
First user_id with more than 10 conversations: f96c8515aa663db23ee086f36b7d3642036d5394bbbeada3fe0c6c8285f4d314 (11 conversations)
First user_id with more than 10 conversations: cbbbb1787dc8a36e05d2acfc474c9fcb32c2

In [12]:
target_user_id = '8fe04885ac7d4510a0f7695261f3285dff4529ce91d15f84dc6c5880977a556a'

topics = []
for conv in dataset.data:
    print(conv.user_id)
    if conv.user_id == target_user_id:
        for message in conv.conversation:
            if "automatic_v0-turn_topic" in message.metadata.keys():
                topic = message.metadata["automatic_v0-turn_topic"].value
                topics.append(topic)

print(f"Number of topics: {len(topics)}")

...
Number of topics: 10


In [13]:
target_user_id = '8fe04885ac7d4510a0f7695261f3285dff4529ce91d15f84dc6c5880977a556a'

for conv in dataset.data:
    print(conv.user_id)
    if conv.user_id == target_user_id:
        for message in conv.conversation:
            if "automatic_v0-turn_topic" in message.metadata.keys():
                metadata = message.metadata
                print(metadata)

8fe04885ac7d4510a0f7695261f3285dff4529ce91d15f84dc6c5880977a556a
{'automatic_v0-prompt_multi_turn_relationship': <src.classes.annotation_record.AnnotationRecord object at 0x34d0d6e30>, 'automatic_v0-prompt_interaction_features': <src.classes.annotation_record.AnnotationRecord object at 0x34d4ed420>, 'automatic_v0-turn_sensitive_use_flags': <src.classes.annotation_record.AnnotationRecord object at 0x34d239d50>, 'automatic_v0-turn_topic': <src.classes.annotation_record.AnnotationRecord object at 0x111f90a00>, 'automatic_v0-prompt_function_purpose': <src.classes.annotation_record.AnnotationRecord object at 0x34d62e110>, 'automatic_v0-prompt_media_format': <src.classes.annotation_record.AnnotationRecord object at 0x34ef30b20>}
{'automatic_v0-prompt_multi_turn_relationship': <src.classes.annotation_record.AnnotationRecord object at 0x34d0d6fe0>, 'automatic_v0-prompt_interaction_features': <src.classes.annotation_record.AnnotationRecord object at 0x34d4ed450>, 'automatic_v0-turn_sensitive_us

In [14]:
target_user_id = '3e7ae36b9ca739b0e16876727814a0e8470c8496aab833c49a5bcc7e77bb7f01'

topics = []
for conv in dataset.data:
    if conv.user_id == target_user_id:
        for message in conv.conversation:
            if "automatic_v0-turn_topic" in message.metadata.keys():
                topic = message.metadata["automatic_v0-turn_topic"].value
                topics.append(topic)

print(f"Number of topics: {len(topics)}")

Number of topics: 56


In [15]:
print(topics)  # Print first 10 topics for verification

[['video games', 'entertainment hobbies leisure'], ['adult illicit content', 'fantasy fiction fanfiction'], ['adult illicit content', 'history', 'literature writing'], ['literature writing', 'history'], ['adult illicit content', 'literature writing'], ['fantasy fiction fanfiction'], ['adult illicit content', 'literature writing', 'geography'], ['fantasy fiction fanfiction'], ['fantasy fiction fanfiction'], ['none'], ['adult illicit content'], ['none'], ['adult illicit content'], ['none'], ['none'], ['none'], ['fantasy fiction fanfiction', 'video games'], ['fantasy fiction fanfiction', 'entertainment hobbies leisure'], ['fantasy fiction fanfiction'], ['fantasy fiction fanfiction'], ['entertainment hobbies leisure', 'adult illicit content'], ['adult illicit content'], ['adult illicit content'], ['fantasy fiction fanfiction'], ['fantasy fiction fanfiction', 'video games'], ['adult illicit content', 'fantasy fiction fanfiction'], ['adult illicit content', 'fantasy fiction fanfiction'], ['f

In [16]:
dataset.data[0].conversation[0].metadata

{'automatic_v0-prompt_multi_turn_relationship': <src.classes.annotation_record.AnnotationRecord at 0x34d0d6e30>,
 'automatic_v0-prompt_interaction_features': <src.classes.annotation_record.AnnotationRecord at 0x34d4ed420>,
 'automatic_v0-turn_sensitive_use_flags': <src.classes.annotation_record.AnnotationRecord at 0x34d239d50>,
 'automatic_v0-turn_topic': <src.classes.annotation_record.AnnotationRecord at 0x111f90a00>,
 'automatic_v0-prompt_function_purpose': <src.classes.annotation_record.AnnotationRecord at 0x34d62e110>,
 'automatic_v0-prompt_media_format': <src.classes.annotation_record.AnnotationRecord at 0x34ef30b20>}

In [17]:
import json

with open(PATH_TO_LANGUAGE_ANNOTATIONS, 'r', encoding='utf-8') as f:
    data = json.load(f)  # Load entire file as one JSON object

target_id_to_language = {
    ann['target_id']: ann['value']
    for ann in data['annotations']
}

id_to_language = {}
for target_id, language in target_id_to_language.items():
    try:
        print(f"{target_id}: {language[0]}")
        id_to_language[target_id] = language[0]
    except Exception as e:
        print(f"Error processing target_id {target_id}: {e}")

wildchat_553847317a397b5def89dae32fe9defd-0: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-1: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-2: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-3: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-4: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-5: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-6: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-7: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-8: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-9: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-10: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-11: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-12: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-13: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-14: CHINESE
wildchat_553847317a397b5def89dae32fe9defd-15: CHINESE
wildchat_cead929b2b15f94b18de7a7eaa5fb733-0: ENGLISH
wildchat_cead929b2b15f94b18de7a7eaa5fb733-1: ENGLISH
wildchat_cead929b2b15f94b18de7a7eaa5fb73

In [18]:
# Add language annotations
for conv in dataset.data:
    print(vars(conv))
    for message in conv.conversation:
        if message.role == "user":
            message.metadata["language"] = id_to_language.get(conv.conversation_id + "-0", "unknown")
            print(f"Language: {message.metadata['language']}")

{'conversation_id': 'wildchat_553847317a397b5def89dae32fe9defd', 'dataset_id': 'wildchat_1m', 'user_id': '8fe04885ac7d4510a0f7695261f3285dff4529ce91d15f84dc6c5880977a556a', 'time': '2023-04-25T02:20:46+00:00', 'model': 'gpt-3.5-turbo-0301', 'conversation': [<src.classes.message.Message object at 0x111f79e40>, <src.classes.message.Message object at 0x11251a710>, <src.classes.message.Message object at 0x112518d30>, <src.classes.message.Message object at 0x112519c90>, <src.classes.message.Message object at 0x112518850>, <src.classes.message.Message object at 0x11251a020>, <src.classes.message.Message object at 0x11251a170>, <src.classes.message.Message object at 0x11251ad70>, <src.classes.message.Message object at 0x11251bdf0>, <src.classes.message.Message object at 0x112518f10>, <src.classes.message.Message object at 0x112518b80>, <src.classes.message.Message object at 0x112518eb0>, <src.classes.message.Message object at 0x11251a3e0>, <src.classes.message.Message object at 0x11251bd30>, 

In [19]:
ENGLISH_ONLY = True

from collections import defaultdict

messages = defaultdict(str)

for conv in dataset.data:
    for message in conv.conversation:
        if message.role == "user":
            if ENGLISH_ONLY:
                if message.metadata.get("language", "unknown") == "ENGLISH":
                    messages[conv.user_id] += message.content + "\n"
            else:
                messages[conv.user_id] += message.content + "\n"

# If you want to convert back to a normal dict:
messages = dict(messages)

# Example: print first 100 characters of one user’s messages
for uid, text in messages.items():
    print(f"{uid}: {text[:100]}...")
    break

fa795c0023cd320f502366592ffcf73666a86c9eca161387ece66eec1fe8514a: keywords "Carrot shape, mechanical pencil,0.5mm"
write a title and five-bulk descriptions , a long d...


## User Embedding and Clustering

Method:

1. Build a corpus from all user message texts and filtering (length, language)

2. Generate text-embedding-3-large embeddings for the filtered corpus and save the embedding matrix to disk.

3. Fit a BERTopic model (with custom UMAP, HDBSCAN, and CountVectorizer) on the documents using the precomputed embeddings to discover topic clusters.

4. For each topic, sample representative prompts by filtering documents with high topic probability and reasonable length.

5. Use GPT-4o to summarize each topic into a short label and description, parse these into structured category/description fields, and build a dataframe with topic stats, percentages, and example prompts.

In [ ]:
import openai
import os
# replace "..." with your OpenAI key.
os.environ["OPENAI_API_KEY"] = ...
openai.api_key = os.getenv("OPENAI_API_KEY")

from umap import UMAP
from hdbscan import HDBSCAN
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer
from bertopic.backend import OpenAIBackend

In [21]:
messages

{'fa795c0023cd320f502366592ffcf73666a86c9eca161387ece66eec1fe8514a': 'keywords "Carrot shape, mechanical pencil,0.5mm"\nwrite a title and five-bulk descriptions , a long description and some SEO keywords.\nIn japanese\n',
 '3cc9823b60008e82cad53972055bef7ee9900bae7e4dfb14e15e293f05a69dd6': 'Give me some examples of meals with good macros from fast food chains that do not contain beans\n',
 'e483d078a0a90f7684f9950c45a370dfcf70ccdcc792cdbf1756e1fd38ab544c': 'What is the "temperature" in the GPT models?\n\nhow does it work\n',
 'c1dd4cf7cd5e49b5a23e3a135ad7e445b2ad0351807525b2ef25cbdd40b584f8': "what is the Cognosys ai and how does it work?\nI wrote some notes on what to look for and ask during a house viewing with a real estate agent. Please take a look and analyze it for any errors or for ways to improve it such as wording or missing questions/concerts/whatever. Any feedback from you would be valuable. Here's what I have noted:\n\nQuestions to Ask During a House Viewing:\n\n    - Is th

In [22]:
user_ids = list(messages.keys())
corpus = [messages[uid] for uid in user_ids]
print(f"Number of users: {len(corpus)}")
print(f"Number of corpus entries: {len(corpus)}")

filtered_corpus = [text for text in corpus if len(text) < 2000]
print(f"Number of filtered corpus entries: {len(filtered_corpus)}")

doc = filtered_corpus
# doc = filtered_corpus[:500]

client = openai.OpenAI()
embedding_model = OpenAIBackend(client, "text-embedding-3-large", batch_size=1000)
embeddings = embedding_model.embed(doc, verbose=True)

# save embeddings
save_path = ".."
np.save(f"{save_path}/embeddings.npy", embeddings)

Number of users: 1663
Number of corpus entries: 1663
Number of filtered corpus entries: 908


1it [00:04,  4.58s/it]


In [23]:
embeddings

array([[-0.01495944, -0.0149671 , -0.00925768, ..., -0.01610898,
        -0.00856796,  0.00643363],
       [-0.0026818 ,  0.00678737, -0.03262991, ...,  0.0085805 ,
         0.00248292, -0.00628542],
       [-0.02996774, -0.04177321, -0.01148622, ...,  0.01434535,
        -0.00676474,  0.02755557],
       ...,
       [-0.02316142,  0.01664446, -0.03484701, ..., -0.00807504,
        -0.01682424, -0.00205996],
       [ 0.01197786, -0.01002092, -0.01488798, ..., -0.01077164,
        -0.0082875 , -0.00857851],
       [-0.01561403,  0.01024892, -0.01501947, ..., -0.01547247,
        -0.0005627 , -0.03861746]])

In [24]:
# load saved embeddings
embeddings = np.load(f"{save_path}/embeddings.npy")
len(embeddings)
# embeddings

908

In [25]:
client = openai.OpenAI()
embedding_model = OpenAIBackend(client, "text-embedding-3-large", batch_size=1000)
umap_model = UMAP(n_neighbors=20, n_components=5, min_dist=0.0, metric='cosine', random_state=42)
hdbscan_model = HDBSCAN(min_cluster_size=20, metric='euclidean', cluster_selection_method='eom', prediction_data=True)
vectorizer_model = CountVectorizer(stop_words="english", min_df=2, ngram_range=(1, 3))

topic_model = BERTopic(
        embedding_model=embedding_model,
        umap_model=umap_model,
        hdbscan_model=hdbscan_model,
        vectorizer_model=vectorizer_model,

        top_n_words=10,
        verbose=True,
        calculate_probabilities=True
)

topics, probs = topic_model.fit_transform(doc, embeddings=embeddings)

2026-02-18 14:51:10,530 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2026-02-18 14:51:16,224 - BERTopic - Dimensionality - Completed ✓
2026-02-18 14:51:16,225 - BERTopic - Cluster - Start clustering the reduced embeddings
2026-02-18 14:51:16,253 - BERTopic - Cluster - Completed ✓
2026-02-18 14:51:16,255 - BERTopic - Representation - Fine-tuning topics using representation models.
2026-02-18 14:51:16,333 - BERTopic - Representation - Completed ✓


In [26]:
# number of clusters
len(topic_model.get_topic_info())

7

In [27]:
topic_model.get_topic_info()

Topic  Count                                        Name  \
0     -1    315                    -1_write_english_make_10   
1      0    312                      0_code_data_use_return   
2      1    155                 1_write_story_dialogue_make   
3      2     46  2_include_art_generate_generate etsy title   
4      3     29                3_artificial_br_lyrics_write   
5      4     27                4_planet_freedom_lilac_react   
6      5     24              5_media_use_short_social media   

                                      Representation  \
0  [write, english, make, 10, like, answer, does,...   
1  [code, data, use, return, file, 15, function, ...   
2  [write, story, dialogue, make, extremely, man,...   
3  [include, art, generate, generate etsy title, ...   
4  [artificial, br, lyrics, write, latin, music, ...   
5  [planet, freedom, lilac, react, characters, so...   
6  [media, use, short, social media, blog, social...   

                                 Representative_Docs  
0  [You are now TranslatorBot or TB. You are a fo...  
1  ["Hi <PRESIDIO_ANONYMIZED_PERSON>,\nYour Urban...  
2  [This is fictional. Contain content warnings. ...  
3  [Generate an etsy title for a art work that ca...  
4  [Write a CBBC schedule for May 2023\nWrite a C...  
5  [Freedom Planet Girls react to Human Petting A...  
6  [Let's write a blog post that will rank on Goo...

In [28]:
from collections import defaultdict

sampled_prompts = defaultdict(list)
topic_info = topic_model.get_topic_info()
doc_info = topic_model.get_document_info(doc)

for topic_id in topic_info['Topic'][1:]:
    filtered_docs = doc_info[(doc_info['Topic'] == topic_id) &
                             (doc_info['Probability'] >= doc_info['Probability'].quantile(0.8)) &
                             (doc_info['Document'].str.split().str.len() >= 5)]

    res = filtered_docs
    cap = 100
    if len(filtered_docs) >= 20:
        while len(res) < 20:
            res = filtered_docs[
                filtered_docs['Document'].str.split().str.len() <= cap
            ]
            cap += 50

    sampled_docs = res.sample(n=min(20,
                            len(res)),
                            random_state=42,
                            replace=False)

    sampled_prompts[topic_id] = sampled_docs['Document'].tolist()

In [29]:
sampled_prompts[0]

['finish the code:\n//Adds the star ranking of a student for a course.\n//If the student or the course does not exist, return false.\n//If the student or the course does not exist, return false.\n//Else if the student already has a star ranking for that course then return return false.\n//Else, add a star ranking, update the stars_count of the course, and increase by one the ranks_count of the student and return true.\n\n// IMPORTANT: Always add in a new StarRank at the end of the list\n\n// @param: student_head points to the head of Student list\n// @param: the id of the student (sid)\n// @param: course_array the array of pointers for the Course\n// @param: the id of the course the student ranks (course_id)\n// @param: the number of courses in the site\n// @param: the rating which is a between 1 and MAX_RANKING_STARS\n// @out: a boolean value indicating whether the insertion was successful\nbool add_star_rank(Student *&student_head, unsigned int sid,\n                 Course **&course

In [30]:
import pickle

with open(f"{save_path}/example_prompts.pkl", 'wb') as f:
    pickle.dump(sampled_prompts, f)

In [31]:
# reduce_outliers - this does not work well for our data
# new_topics = topic_model.reduce_outliers(list(doc), topics , strategy="c-tf-idf", threshold=0.1)
# new_topics = topic_model.reduce_outliers(list(doc), new_topics, strategy="distributions")
# topic_model.update_topics(doc, topics=new_topics)

In [32]:
topic_info = topic_model.get_topic_info()
doc_info = topic_model.get_document_info(list(doc))
topic_info

Topic  Count                                        Name  \
0     -1    315                    -1_write_english_make_10   
1      0    312                      0_code_data_use_return   
2      1    155                 1_write_story_dialogue_make   
3      2     46  2_include_art_generate_generate etsy title   
4      3     29                3_artificial_br_lyrics_write   
5      4     27                4_planet_freedom_lilac_react   
6      5     24              5_media_use_short_social media   

                                      Representation  \
0  [write, english, make, 10, like, answer, does,...   
1  [code, data, use, return, file, 15, function, ...   
2  [write, story, dialogue, make, extremely, man,...   
3  [include, art, generate, generate etsy title, ...   
4  [artificial, br, lyrics, write, latin, music, ...   
5  [planet, freedom, lilac, react, characters, so...   
6  [media, use, short, social media, blog, social...   

                                 Representative_Docs  
0  [You are now TranslatorBot or TB. You are a fo...  
1  ["Hi <PRESIDIO_ANONYMIZED_PERSON>,\nYour Urban...  
2  [This is fictional. Contain content warnings. ...  
3  [Generate an etsy title for a art work that ca...  
4  [Write a CBBC schedule for May 2023\nWrite a C...  
5  [Freedom Planet Girls react to Human Petting A...  
6  [Let's write a blog post that will rank on Goo...

In [33]:
# save the model for future analysis
topic_model.save(
    path=f"{save_path}/model",
    serialization="safetensors",
    save_ctfidf=True
)

# Summarize Category Names

In [34]:
def summarize_topic(prompts):
    input_text = "Based on the sampled prompts below, extract a short but highly descriptive \
                  topic label of at most 5 words and a short description of this category in \
                  two sentences:\n\n" + "\n\n".join(prompts)
    client = openai.OpenAI()

    response = client.chat.completions.create(
        model="gpt-4o",
        messages=[
            {"role": "system", "content": "You help summarize the category of the given prompts. \
              Make sure it is in the following format: The topic of doc is: '...'. Description: '...'."},
            {"role": "user", "content": input_text}
        ],
        temperature=0
    )

    return response.choices[0].message.content

summaries = {}
for topic_id, prompts in sampled_prompts.items():
    summary = summarize_topic(prompts)
    summaries[topic_id] = summary

In [35]:
def extract_category(summary):
    try:
        return re.search(r"is: '(.*?)'", summary).group(1)
    except AttributeError:
        try:
            return re.search(r"'(.*?)'. ", summary).group(1)
        except AttributeError:
            print(f"Regex failed for: {list(summaries.keys())[list(summaries.values()).index(summary)]}")
            return None
def extract_description(summary):
    try:
        return re.search(r"Description: '(.*?)'", summary).group(1)
    except AttributeError:
        try:
            return re.search(r"Description: (.*?)", summary).group(1)
        except AttributeError:
            print(f"Regex failed for: {summary}")
            return None

In [36]:
summaries[-1] = "The topic of doc is 'Miscellaneous Categories'. Description: 'They are outliers in the topic modeling process'."
summaries_df = pd.DataFrame(list(summaries.items()), columns=['Topic', 'Summary'])
summaries_df['Category'] = summaries_df['Summary'].apply(extract_category)
summaries_df['Description'] = summaries_df['Summary'].apply(extract_description)

topic_info_modified = topic_info[['Topic', 'Count']]
summaries_df = summaries_df.merge(topic_info_modified, on='Topic')[['Topic', 'Category', 'Description', 'Count']]
summaries_df['Percentage'] = summaries_df['Count'] / summaries_df['Count'].sum()
summaries_df['Example Prompt'] = summaries_df.apply(lambda x: sampled_prompts[x.Topic], axis=1)
summaries_df['Example Prompt'] = summaries_df['Example Prompt'].str.join('|||')

In [37]:
summaries_df

Topic                                       Category  \
0      0              Technical and Communication Tasks   
1      1             Transformation and Fantasy Stories   
2      2  SEO Product Descriptions and Art Descriptions   
3      3                    Creative Writing and Lyrics   
4      4                 Crossover Fanfiction Reactions   
5      5              Business and Marketing Strategies   
6     -1                       Miscellaneous Categories   

                                         Description  Count  Percentage  \
0  The document contains a variety of prompts rel...    312    0.343612   
1  The prompts primarily focus on transformation ...    155    0.170705   
2  The document focuses on generating SEO-optimiz...     46    0.050661   
3  The prompts focus on creating various forms of...     29    0.031938   
4  This category involves characters from various...     27    0.029736   
5  This document encompasses a variety of prompts...     24    0.026432   
6    They are outliers in the topic modeling process    315    0.346916   

                                      Example Prompt  
0  finish the code:\n//Adds the star ranking of a...  
1  Write a story about a man alone in his apartme...  
2  keywords "Carrot shape, mechanical pencil,0.5m...  
3  write a sad rap with big words about how life ...  
4  Freedom Planet Girls react to Human Petting A ...  
5  Analyze real-time market trends and suggest th...  
6

In [38]:
# save if needed
summaries_df.to_csv(f"{save_path}/narrow_categories.csv", index=False)

## User Preference Analysis

In [39]:
preference_dimensions = {
    "expertise": ["responses that can be easily understood by beginners", "responses with expert-level knowledge"],
    "informativeness": ["responses that provide concise information", "responses that provide in-depth and comprehensive information"],
    "tone": ["responses with a casual and friendly tone", "responses with a formal and professional tone"],
    "structure": ["responses that are structured with a clear and logical flow", "responses that are unstructured and free-form"],
    "creativity": ["responses that are highly creative and original", "responses that are more conventional and predictable"],
    "engagement": ["responses that encourage user interaction and engagement", "responses that are more informative and less interactive"],
}

In [40]:
user_messages = doc[:50]

In [41]:
def classify_user_preferences(user_messages, client, preference_dimensions):
    """
    Classify user preferences for each document using GPT-4o.
    
    Args:
        user_messages: List of strings, each containing concatenated user messages
        client: OpenAI client instance
        preference_dimensions: Dictionary of preference dimensions
    
    Returns:
        List of dictionaries containing classifications for each user
    """
    results = []
    
    for idx, messages in enumerate(user_messages):
        print(f"Processing user {idx + 1}/{len(user_messages)}...")
        
        # Create the classification prompt
        prompt = f"""Analyze the following user messages and classify their preferences across different dimensions.

User Messages:
{messages}

For each dimension below, determine whether the user prefers option 1, option 2, or shows no clear preference based on their message patterns, questions, and interaction style.

Preference Dimensions:
"""
        
        for dimension, (pref1, pref2) in preference_dimensions.items():
            prompt += f"\n{dimension.upper()}:\n- Preference 1: {pref1}\n- Preference 2: {pref2}\n"
        
        prompt += """
Please respond in the following JSON format:
{
    "expertise": "preference 1" | "preference 2" | "no clear preference",
    "informativeness": "preference 1" | "preference 2" | "no clear preference",
    "tone": "preference 1" | "preference 2" | "no clear preference",
    "structure": "preference 1" | "preference 2" | "no clear preference",
    "creativity": "preference 1" | "preference 2" | "no clear preference",
    "engagement": "preference 1" | "preference 2" | "no clear preference"
}

Only output the JSON, nothing else."""
        
        try:
            # Call GPT-4o
            response = client.chat.completions.create(
                model="gpt-4o",
                messages=[
                    {"role": "system", "content": "You are an expert at analyzing user communication patterns and preferences. Provide classifications in valid JSON format only."},
                    {"role": "user", "content": prompt}
                ],
                temperature=0.3,
                response_format={"type": "json_object"}
            )
            
            # Parse the response
            import json
            classification = json.loads(response.choices[0].message.content)
            
            results.append({
                "user_index": idx,
                "classifications": classification
            })
            
        except Exception as e:
            print(f"Error processing user {idx}: {e}")
            results.append({
                "user_index": idx,
                "classifications": {dim: "error" for dim in preference_dimensions.keys()}
            })
    
    return results


# Run the classification
results = classify_user_preferences(user_messages, client, preference_dimensions)

Processing user 1/50...
Processing user 2/50...
Processing user 3/50...
Processing user 4/50...
Processing user 5/50...
Processing user 6/50...
Processing user 7/50...
Processing user 8/50...
Processing user 9/50...
Processing user 10/50...
Processing user 11/50...
Processing user 12/50...
Processing user 13/50...
Processing user 14/50...
Processing user 15/50...
Processing user 16/50...
Processing user 17/50...
Processing user 18/50...
Processing user 19/50...
Processing user 20/50...
Processing user 21/50...
Processing user 22/50...
Processing user 23/50...
Processing user 24/50...
Processing user 25/50...
Processing user 26/50...
Processing user 27/50...
Processing user 28/50...
Processing user 29/50...
Processing user 30/50...
Processing user 31/50...
Processing user 32/50...
Processing user 33/50...
Processing user 34/50...
Processing user 35/50...
Processing user 36/50...
Processing user 37/50...
Processing user 38/50...
Processing user 39/50...
Processing user 40/50...
Processin

In [42]:
# Print the final results
print("FINAL CLASSIFICATION RESULTS")

for dimension, (pref1_desc, pref2_desc) in preference_dimensions.items():
    # Count preferences for this dimension
    pref1_count = sum(1 for r in results if r["classifications"].get(dimension) == "preference 1")
    pref2_count = sum(1 for r in results if r["classifications"].get(dimension) == "preference 2")
    no_pref_count = sum(1 for r in results if r["classifications"].get(dimension) == "no clear preference")

    # Print the results
    print(f'"{dimension}":')
    print(f'  * "{pref1_desc}" - {pref1_count} users')
    print(f'  * "{pref2_desc}" - {pref2_count} users')
    print(f'  * "no clear preference" - {no_pref_count} users')
    print()

FINAL CLASSIFICATION RESULTS
"expertise":
  * "responses that can be easily understood by beginners" - 7 users
  * "responses with expert-level knowledge" - 34 users
  * "no clear preference" - 9 users

"informativeness":
  * "responses that provide concise information" - 19 users
  * "responses that provide in-depth and comprehensive information" - 29 users
  * "no clear preference" - 2 users

"tone":
  * "responses with a casual and friendly tone" - 14 users
  * "responses with a formal and professional tone" - 21 users
  * "no clear preference" - 15 users

"structure":
  * "responses that are structured with a clear and logical flow" - 40 users
  * "responses that are unstructured and free-form" - 5 users
  * "no clear preference" - 5 users

"creativity":
  * "responses that are highly creative and original" - 22 users
  * "responses that are more conventional and predictable" - 13 users
  * "no clear preference" - 15 users

"engagement":
  * "responses that encourage user interacti